# Задание 10
1. Построить дерево классификации для набора данных из статьи:
ЭЛЕКТРОННО-МИКРОЗОНДОВЫЙ АНАЛИЗ ФОРМОВОЧНЫХ МАСС...pdf  (данные в Таблице 3).
Классом считать территорию + тип керамики
2. Оценить качество классификации.
3. Оценить значимость переменных.


In [74]:
import pandas as pd
import matplotlib

matplotlib.style.use('ggplot')
%matplotlib inline

In [75]:
df = pd.read_csv('file.csv', sep=";", header = 0, index_col=False)
df['Класс'] = df['Территория'] + '-' + df['Тип керамики']

In [76]:
df.head()

Территория Тип керамики  Номер образца     K    Ca  SiO2    Na   K.1  \
0  О-в Сахалин     Охотский             31  0.05  0.04  0.94  0.48  0.48   
1  О-в Сахалин     Охотский             71  0.05  0.06  0.88  0.45  0.25   
2  О-в Сахалин     Охотский             11  0.16  0.06  0.78  0.40  0.43   
3  О-в Сахалин     Охотский            131  0.20  0.05  0.75  0.54  0.37   
4  О-в Сахалин     Охотский            141  0.09  0.01  0.89  0.43  0.50   

   Ca.1    Mg    Ti    Fe                 Класс  
0  0.04  0.01  0.16  0.83  О-в Сахалин-Охотский  
1  0.30  0.02  0.20  0.78  О-в Сахалин-Охотский  
2  0.17  0.03  0.13  0.83  О-в Сахалин-Охотский  
3  0.09  0.00  0.14  0.86  О-в Сахалин-Охотский  
4  0.08  0.03  0.12  0.85  О-в Сахалин-Охотский

In [77]:
df.shape

(79, 13)

In [78]:
df.dtypes

Территория        object
Тип керамики      object
Номер образца      int64
K                float64
Ca               float64
SiO2             float64
Na               float64
K.1              float64
Ca.1             float64
Mg               float64
Ti               float64
Fe               float64
Класс             object
dtype: object

In [79]:
X = df.iloc[:, 3:-1]
y = df['Класс']

In [80]:
from sklearn.tree import DecisionTreeClassifier

model = DecisionTreeClassifier(random_state=42,
                               criterion='gini',
                               max_depth=5,
                               min_samples_split=2,
                               min_samples_leaf=2,
                               class_weight=None
                              )

In [81]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=42,
                                                    test_size=0.2)
model.fit(X_train, y_train)

DecisionTreeClassifier(max_depth=5, min_samples_leaf=2, random_state=42)

In [82]:
from IPython.display import Image
from sklearn.tree import export_graphviz
from subprocess import call

export_graphviz(model,
                out_file='tree.dot',
                class_names=None,
                label='all',
                filled=True,
                impurity=True,
                node_ids=True,
                proportion=True,
                rotate=True,
               )

In [83]:
call(['dot', '-Tpng', 'tree.dot', '-o', 'tree.png', '-Gdpi=600'])

0

In [84]:
Image(filename = 'tree.png')

In [85]:
y_pred = model.predict(X_test)

In [86]:
from sklearn import metrics

print(metrics.classification_report(y_test, y_pred, zero_division=0))

                       precision    recall  f1-score   support

 Г. Вакканай-Охотский       0.00      0.00      0.00         2
Г. Вакканай-Сусуйский       0.00      0.00      0.00         5
    Г. Есаши-Охотский       0.00      0.00      0.00         0
   О-в Ребун-Охотский       0.33      0.33      0.33         3
  О-в Рисири-Охотский       0.00      0.00      0.00         1
 О-в Рисири-Сусуйский       0.00      0.00      0.00         1
 О-в Сахалин-Охотский       0.80      1.00      0.89         4

             accuracy                           0.31        16
            macro avg       0.16      0.19      0.17        16
         weighted avg       0.26      0.31      0.28        16



In [87]:
# conf_mat = metrics.confusion_matrix(y_test, y_pred, labels=model.classes_)
# conf_mat = pd.DataFrame(conf_mat, index=model.classes_, columns=model.classes_)
metrics.confusion_matrix(y_test, y_pred)

array([[0, 0, 0, 2, 0, 0, 0],
       [0, 0, 1, 0, 1, 2, 1],
       [0, 0, 0, 0, 0, 0, 0],
       [1, 0, 0, 1, 1, 0, 0],
       [1, 0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 1, 0, 0],
       [0, 0, 0, 0, 0, 0, 4]])

In [88]:
pd.DataFrame({'feature': X.columns,
              'importance': model.feature_importances_}).sort_values('importance', ascending=False)

feature  importance
7      Ti    0.311494
6      Mg    0.252787
2    SiO2    0.188779
3      Na    0.095612
0       K    0.086541
8      Fe    0.038873
1      Ca    0.012958
4     K.1    0.012958
5    Ca.1    0.000000